# Practica 2

In [33]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import RobustScaler
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score, calinski_harabasz_score, davies_bouldin_score, silhouette_samples
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import os
import warnings
warnings.filterwarnings('ignore')

## Extraccion de datos

###  Carga y preparación de datos por persona

En esta celda se recorre la estructura de carpetas del conjunto de datos, donde cada subcarpeta representa a una persona (`sub_XX`). Para cada persona:

1. Se cargan todos los archivos `.csv` que representan diferentes trayectorias de marcha.
2. Se concatenan las trayectorias en un único DataFrame por persona.
3. Se aplica la normalización **RobustScaler**, que corrige diferencias de escala entre personas (por ejemplo, altura o proporciones corporales) y reduce la influencia de outliers.

El objetivo de esta etapa es preparar los datos para que los algoritmos de clustering puedan agrupar movimientos en función del **comportamiento corporal**, y no por el tamaño del cuerpo o por cómo se desplace la persona en el entorno.

#### ¿Por qué se utiliza `RobustScaler` en lugar de `StandardScaler` o `Normalizer`?

- **`RobustScaler`** utiliza la **mediana** y el **rango intercuartílico (IQR)** para escalar los datos, lo que lo hace mucho **más resistente a valores atípicos** (outliers). Esto es especialmente útil en movimiento humano, donde una articulación puede moverse de forma puntual de forma muy extrema (por ejemplo, un brazo muy levantado).
  
- **`StandardScaler`** asume que los datos tienen distribución normal (media y desviación típica). En señales de movimiento real, esta suposición no siempre se cumple, y puede distorsionar la escala si hay outliers.

- **`Normalizer`** transforma cada vector a norma 1 (longitud unitaria). Esto es útil cuando importa la dirección del vector más que su escala, pero **no es apropiado para coordenadas espaciales**, ya que distorsionaría la posición relativa de las articulaciones.

En resumen, `RobustScaler` es la mejor opción para este problema porque ofrece **estabilidad frente a outliers** sin asumir una distribución específica de los datos, manteniendo la estructura relativa del movimiento.

In [ ]:
# Ruta base del dataset
base_path = r'C:\uni\grado\2024-2025\IA\dataset\data'
print("\nCargando y normalizando datos por persona...")
all_data = []
for sub_dir in os.listdir(base_path):
    if sub_dir.startswith('sub_'):
        sub_path = os.path.join(base_path, sub_dir)
        data_person_frames = []

        for rec_file in os.listdir(sub_path):
            if rec_file.endswith('.csv'):
                file_path = os.path.join(sub_path, rec_file)
                
                # Cargar CSV
                df = pd.read_csv(file_path)
                data_person_frames.append(df)

        if data_person_frames:
            df_person = pd.concat(data_person_frames, ignore_index=True)

            # Aplicar RobustScaler por persona directamente
            scaler = RobustScaler()
            data_scaled = scaler.fit_transform(df_person)

            # Convertir a DataFrame
            df_scaled = pd.DataFrame(data_scaled, columns=df_person.columns)
            all_data.append(df_scaled)

# Concatenar todos los datos normalizados
all_data = pd.concat(all_data, ignore_index=True)
print("Datos normalizados por persona. Shape final:", all_data.shape)
all_data.head()


Cargando y normalizando datos por persona...
Datos normalizados por persona. Shape final: (910180, 72)


pelvis_x  pelvis_y  pelvis_z      L5_x      L5_y      L5_z      L3_x  \
0  0.090030  1.941995  0.514551  0.090833  1.948008  0.518941  0.091032   
1  0.090002  1.941850  0.516784  0.090808  1.947864  0.521032  0.091014   
2  0.089973  1.941704  0.519017  0.090784  1.947720  0.523123  0.090996   
3  0.089943  1.941557  0.521038  0.090758  1.947573  0.525036  0.090977   
4  0.089912  1.941404  0.522846  0.090731  1.947422  0.526737  0.090956   

       L3_y      L3_z     T12_x  ...  lowerLegLeft_z  footLeft_x  footLeft_y  \
0  1.951956  0.580641  0.091632  ...        0.065333    0.092041    1.929997   
1  1.951793  0.582786  0.091620  ...        0.065732    0.092037    1.929985   
2  1.951630  0.584931  0.091608  ...        0.066131    0.092032    1.929974   
3  1.951467  0.586866  0.091595  ...        0.066065    0.092029    1.929962   
4  1.951302  0.588624  0.091581  ...        0.065466    0.092028    1.929950   

   footLeft_z  toeLeft_x  toeLeft_y  toeLeft_z     vel_x     vel_y     vel_z  
0   -0.471855   0.085053   1.866259   0.114692 -0.017913 -0.012653  0.001812  
1   -0.471305   0.085052   1.866250   0.113151 -0.017555 -0.012689  0.002843  
2   -0.470754   0.085051   1.866242   0.111633 -0.017196 -0.012725  0.003878  
3   -0.470323   0.085051   1.866234   0.110115 -0.016949 -0.012847  0.004981  
4   -0.470055   0.085053   1.866226   0.108642 -0.016991 -0.013189  0.006794  

[5 rows x 72 columns]

> Cada fila representa una medición individual en el tiempo, con información detallada de la posición y velocidad en 3D de múltiples segmentos corporales.


In [35]:
# Imprimir los nombres de las etiquetas (columnas)
print("Nombres de las etiquetas:")
for i, label in enumerate(all_data):
    print(f"{i}: {label}")


Nombres de las etiquetas:
0: pelvis_x
1: pelvis_y
2: pelvis_z
3: L5_x
4: L5_y
5: L5_z
6: L3_x
7: L3_y
8: L3_z
9: T12_x
10: T12_y
11: T12_z
12: T8_x
13: T8_y
14: T8_z
15: neck_x
16: neck_y
17: neck_z
18: head_x
19: head_y
20: head_z
21: shoulderRight_x
22: shoulderRight_y
23: shoulderRight_z
24: upperArmRight_x
25: upperArmRight_y
26: upperArmRight_z
27: forearmRight_x
28: forearmRight_y
29: forearmRight_z
30: handRight_x
31: handRight_y
32: handRight_z
33: shoulderLeft_x
34: shoulderLeft_y
35: shoulderLeft_z
36: upperArmLeft_x
37: upperArmLeft_y
38: upperArmLeft_z
39: forearmLeft_x
40: forearmLeft_y
41: forearmLeft_z
42: handLeft_x
43: handLeft_y
44: handLeft_z
45: upperLegRight_x
46: upperLegRight_y
47: upperLegRight_z
48: lowerLegRight_x
49: lowerLegRight_y
50: lowerLegRight_z
51: footRight_x
52: footRight_y
53: footRight_z
54: toeRight_x
55: toeRight_y
56: toeRight_z
57: upperLegLeft_x
58: upperLegLeft_y
59: upperLegLeft_z
60: lowerLegLeft_x
61: lowerLegLeft_y
62: lowerLegLeft_z
63:

### Eliminación de correlación espacial entre articulaciones

En este apartado se busca reducir la **correlación espacial artificial** entre las coordenadas de distintas articulaciones, que puede deberse a que todas comparten un mismo marco de referencia (por ejemplo, el sistema global de coordenadas).

Para ello:

- Se crea una copia del DataFrame original llamada `resta`.
- Para cada coordenada (x, y, z), se resta la posición de la **pelvis** a todas las demás articulaciones. Esto se hace para que las posiciones pasen a estar **relativas a la pelvis**, eliminando así el efecto del movimiento global del cuerpo.
- Finalmente, se calcula la **matriz de correlación** entre las primeras 18 columnas (probablemente las articulaciones más importantes o del tronco superior).




In [36]:
resta = all_data.copy()
for i in range(3):
  # Obtener las columnas correspondientes a cada coordenada (x,y,z)
  cols = all_data.iloc[:,i:i+1].to_numpy()
  # Restar la posición de la pelvis a cada articulación para esa coordenada
  resta.iloc[:,i:-3:3] = all_data.iloc[:,i:-3:3].sub(cols.flatten(), axis=0)



A continuacion procedemos a comparar las matrices de correlacion para ver los efectos

In [37]:
# Calcular matriz de correlación original
corrs_original = all_data.iloc[:, :].corr()

# Calcular matriz de correlación tras la resta
corrs_resta = resta.iloc[:, :].corr()

# Convertir las matrices de correlación a numpy arrays
corrs_original_np = corrs_original.to_numpy()
corrs_resta_np = corrs_resta.to_numpy()
heatmap_labels = corrs_original.columns.tolist()


# Crear subplot interactivo


fig = make_subplots(rows=1, cols=2, subplot_titles=("Correlación Original", "Correlación después de la resta"),
                    shared_yaxes=True)

# Mapa de calor original
fig.add_trace(
    go.Heatmap(z=corrs_original_np, x=heatmap_labels, y=heatmap_labels, colorscale='RdBu', zmin=-1, zmax=1, colorbar=dict(title="Correlación")),
    row=1, col=1
)

# Mapa de calor tras la resta
fig.add_trace(
    go.Heatmap(z=corrs_resta_np, x=heatmap_labels, y=heatmap_labels, colorscale='RdBu', zmin=-1, zmax=1, showscale=False),
    row=1, col=2
)

fig.update_layout(
    title="Comparación de Correlaciones antes y después de eliminar la referencia global",
    height=700,
    width=1400
)

fig.show()


> En el mapa de calor de la izquierda (correlación original), se observa una alta correlación entre casi todas las articulaciones, lo cual es esperable dado que todas comparten un marco de referencia global común.

> Tras eliminar la referencia global (derecha), las correlaciones disminuyen notablemente y aparecen patrones más diferenciados. Esto indica que ahora se están capturando relaciones más reales entre los movimientos relativos de las articulaciones, lo que es más útil para análisis biomecánicos o de aprendizaje automático.


### Ventaneo temporal de los datos

En este paso se aplica un proceso de **ventaneo** (segmentación temporal) sobre los datos preprocesados para estructurarlos en bloques o fragmentos de duración fija, adecuados para su análisis o entrada en modelos de aprendizaje automático.

- Se define una frecuencia de muestreo de `60 Hz` (60 muestras por segundo) como se idico en el enunciado.
- Cada ventana tendrá una duración de `4 segundos`, lo que equivale a `240 muestras` por ventana (`60 * 4`).
- Se recorre el conjunto de datos con un paso igual al tamaño de la ventana (ventaneo sin solapamiento), extrayendo fragmentos consecutivos del DataFrame `resta`.
- Cada fragmento (ventana) es almacenado como un array independiente dentro de una lista.
- Finalmente, se convierte la lista a un array de NumPy tridimensional: `(n_ventanas, muestras_por_ventana, n_variables)`.

Esto estructura los datos en un formato adecuado para tareas como clasificación o detección de patrones en series temporales.


In [38]:
freq = 60
segundos = 4
ventana = freq*segundos
ventanas = []

for i in range(0, len(resta)-ventana+1,ventana):
  ventanas.append(resta.iloc[i:+i+ventana])

ventanas = np.array(ventanas)
ventanas.shape

(3792, 240, 72)

### **Normalización del origen en la pelvis**
- Se toma la posición (x, y, z) de la **pelvis en el primer frame** de la ventana como nuevo origen `(0, 0, 0)`.
- Esta posición se **resta a todas las articulaciones** de todos los frames dentro de la ventana, de forma vectorizada.
- El resultado es que cada ventana comienza desde una misma referencia espacial, lo cual es útil para modelar movimientos relativos de manera coherente.


In [39]:
ventanas_normalizadas = []

for ventana in ventanas:
    # 1. Normalización del origen en (0,0,0) con respecto a la pelvis en el primer frame
    ventana_norm = ventana.copy()
    
    pelvis_coords = ventana[0, :3]  # (x, y, z) de la pelvis en el primer frame
    n_articulaciones = ventana.shape[1] // 3
    
    # Construimos un vector que repite pelvis_coords para cada articulación (x, y, z, x, y, z, ...)
    pelvis_tile = np.tile(pelvis_coords, n_articulaciones)
    
    # Restamos el origen a cada frame
    ventana_norm = ventana_norm - pelvis_tile
    
    ventanas_normalizadas.append(ventana_norm)

ventanas_normalizadas = np.array(ventanas_normalizadas)
print("Forma final:", ventanas_normalizadas.shape)


Forma final: (3792, 240, 72)


## Extracción de Características

En esta sección se implementan diversas técnicas para transformar las señales temporales de movimiento (coordenadas articulares) en vectores de características numéricas que puedan ser utilizados por modelos de aprendizaje automático o análisis posteriores.

Para organizar el proceso de manera estructurada y reutilizable, se definen diferentes funciones especializadas:

- **`calculate_hjorth_parameters`**: calcula tres parámetros temporales que describen la complejidad y variabilidad de la señal.
- **`extract_frequency_features`**: obtiene características espectrales a partir de la Transformada Rápida de Fourier (FFT).
- **`extract_statistical_features`**: extrae estadísticas descriptivas de la señal (media, desviación, etc.).
- **`extract_features`**: función principal que combina todas las anteriores para generar un vector completo de características para una señal 


### Cálculo de Parámetros de Hjorth

Se define una función para calcular los tres **parámetros de Hjorth** de una señal temporal:

- **Activity**: varianza de la señal original, indica su potencia total.
- **Mobility**: relación entre la varianza de la primera derivada y la varianza de la señal original. Representa qué tan rápido cambia la señal.
- **Complexity**: compara la movilidad de la primera derivada con la de la señal original. Indica qué tan compleja es la forma de la señal.

Estos parámetros son comúnmente usados en análisis de bioseñales (como EEG, movimiento, etc.) para describir la dinámica de una señal sin necesidad de transformaciones complejas.



In [40]:
def calculate_hjorth_parameters(signal):
    """
    Calcula los parámetros de Hjorth para una señal temporal.
    
    Los parámetros de Hjorth son:
    - Activity: Varianza de la señal, representa la potencia
    - Mobility: Raíz cuadrada del ratio de varianzas entre la primera derivada y la señal original
    - Complexity: Ratio entre la movilidad de la primera derivada y la movilidad de la señal original
    
    Args:
        signal (array): Señal temporal de entrada
        
    Returns:
        list: Lista con los tres parámetros de Hjorth [activity, mobility, complexity]
    """
    d1 = np.diff(signal, prepend=signal[0])
    d2 = np.diff(d1, prepend=d1[0])
    activity = np.var(signal)
    var1 = np.var(d1)
    var2 = np.var(d2)
    mobility = np.sqrt(var1 / activity) if activity != 0 else 0
    complexity = np.sqrt(var2 / var1) / mobility if var1 != 0 and mobility != 0 else 0
    return [activity, mobility, complexity]

### Extracción de Características en el Dominio de la Frecuencia

Esta función calcula características relevantes a partir de la **Transformada Rápida de Fourier (FFT)** de una señal temporal:

- **Dominant Frequency**: frecuencia con mayor amplitud.
- **Mean Frequency**: frecuencia media ponderada por amplitud.
- **Frequency Std**: desviación estándar de las frecuencias, también ponderada.

Estas características ayudan a capturar el contenido rítmico u oscilatorio de la señal, lo cual es útil en análisis de movimiento periódico o para distinguir patrones dinámicos.


In [41]:
def extract_frequency_features(signal):
    """
    Extrae características en el dominio de la frecuencia (FFT).
    
    Args:
        signal: señal temporal
    Returns:
        lista de características de frecuencia
    """
    fft_vals = np.abs(np.fft.fft(signal))
    freqs = np.fft.fftfreq(len(signal))

    # Filtrar solo frecuencias positivas
    pos_mask = freqs > 0
    fft_vals = fft_vals[pos_mask]
    freqs = freqs[pos_mask]

    # Si la FFT es cero, retornar valores por defecto
    if len(fft_vals) == 0:
        return [0.0, 0.0, 0.0]

    # Características de frecuencia
    dominant_freq = freqs[np.argmax(fft_vals)]
    mean_freq = np.sum(freqs * fft_vals) / np.sum(fft_vals) if np.sum(fft_vals) !=0 else 0
    freq_std = np.sqrt(np.sum((freqs - mean_freq) ** 2 * fft_vals) / np.sum(fft_vals)) if np.sum(fft_vals) !=0 else 0

    return [dominant_freq, mean_freq, freq_std]


### Extracción de Características Estadísticas

Este bloque define una función que calcula un conjunto de estadísticas descriptivas sobre la señal:

- Media, desviación estándar, mínimo, máximo
- **Percentiles 25 y 75**, así como el **rango intercuartílico (IQR)**
- **Número de cruces por el valor medio** (zero crossings), que indica variabilidad

Estas características resumen la distribución y comportamiento básico de la señal en el tiempo.


In [42]:
def extract_statistical_features(signal):
    """
    Extrae características estadísticas de una señal temporal.
    
    Args:
        signal: array de numpy con la señal temporal
        
    Returns:
        lista con las siguientes características:
            - media
            - desviación estándar  
            - valor mínimo
            - valor máximo
            - percentil 25
            - percentil 75 
            - rango intercuartílico (IQR)
            - número de cruces por la media
    """
    mean = np.mean(signal)
    std = np.std(signal)
    minimum = np.min(signal)
    maximum = np.max(signal)
    q25, q75 = np.percentile(signal, [25, 75])
    iqr = q75 - q25
    zero_crossings = np.sum(np.diff(np.signbit(signal - mean)))
    
    return [mean, std, minimum, maximum, q25, q75, iqr,zero_crossings]

### Función Unificada de Extracción de Características

Se define una función para **agrupar todas las características extraídas** de una señal en un único vector:

- Características estadísticas
- Energía total de la señal (suma de cuadrados)
- Parámetros de Hjorth
- Características en frecuencia



In [43]:

def extract_features(signal):
    """
    Extrae un conjunto completo de características de una señal temporal.
    
    Args:
        signal: array de numpy con la señal temporal
        
    Returns:
        lista con las siguientes características concatenadas:
            - Características estadísticas
            - Energía total de la señal
            - Parámetros de Hjorth
            - Características en frecuencia
    """
    stats_features = extract_statistical_features(signal)
    energy = np.sum(signal ** 2)
    hjorth_params = calculate_hjorth_parameters(signal)
    freq_features = extract_frequency_features(signal)

    return stats_features + [energy] + hjorth_params + freq_features

### Extracción de Características sobre Ventanas Normalizadas

Este bloque aplica la función `extract_features` a cada coordenada de cada ventana temporal:

- Se itera sobre todas las ventanas normalizadas (cada una representa un segmento de movimiento).
- Para cada coordenada (columna), se calcula el vector de características completo.
- Las características se almacenan para formar una matriz final `features`, donde cada fila representa una ventana y cada columna una característica.

El resultado es una representación estructurada que puede usarse directamente como entrada para modelos de clasificación, clustering o aprendizaje automático.


In [44]:
# Extraer características para todas las ventanas y coordenadas
features = []
for window in ventanas_normalizadas:
    window_features = []
    for j in range(window.shape[1]):
        signal = window[:, j]
        window_features.extend(extract_features(signal))
    features.append(window_features)

features = np.array(features)
print("Shape de las características:", features.shape)


Shape de las características: (3792, 1080)


## Juntar Datos

En esta etapa se consolidan todas las características extraídas de las señales de movimiento en un único DataFrame estructurado. Al guardar los datos en un archivo `.csv`, facilitamos su almacenamiento, reutilización y compartición sin tener que repetir el proceso de extracción cada vez.




In [45]:
# Crear nombres de columnas para las características
feature_names = [f'feature_{i}' for i in range(features.shape[1])]

# Crear el DataFrame
df_features = pd.DataFrame(features, columns=feature_names)

# Guardar en CSV
df_features.to_csv('features3.csv', index=False)
print("Archivo CSV creado exitosamente")


Archivo CSV creado exitosamente


In [46]:
# Leer el archivo CSV de características
features = pd.read_csv('features.csv')
print("Dimensiones del DataFrame:", features.shape)
print("\nPrimeras 5 filas:")
print(features.head())


Dimensiones del DataFrame: (3792, 1080)

Primeras 5 filas:
   feature_0  feature_1  feature_2  feature_3  feature_4  feature_5  \
0        0.0        0.0        0.0        0.0        0.0        0.0   
1        0.0        0.0        0.0        0.0        0.0        0.0   
2        0.0        0.0        0.0        0.0        0.0        0.0   
3        0.0        0.0        0.0        0.0        0.0        0.0   
4        0.0        0.0        0.0        0.0        0.0        0.0   

   feature_6  feature_7  feature_8  feature_9  ...  feature_1070  \
0        0.0        0.0        0.0        0.0  ...      0.013154   
1        0.0        0.0        0.0        0.0  ...      0.113696   
2        0.0        0.0        0.0        0.0  ...      0.100105   
3        0.0        0.0        0.0        0.0  ...      0.119487   
4        0.0        0.0        0.0        0.0  ...      0.101107   

   feature_1071  feature_1072  feature_1073  feature_1074  feature_1075  \
0      0.049629          18.0 

## PCA

#### Reducción de dimensionalidad con PCA y visualización

Se aplica el Análisis de Componentes Principales (PCA) para reducir la dimensionalidad de las características extraídas. En este caso, se conservan suficientes componentes como para explicar el 95% de la varianza total de los datos. Posteriormente, se visualizan las primeras tres componentes principales en un gráfico 3D, lo que permite observar posibles agrupaciones, tendencias o estructuras latentes en los datos.


In [47]:
pca = PCA(n_components=0.95, random_state=42)
features_pca = pca.fit_transform(features)

# Crear DataFrame con componentes principales
df_pca = pd.DataFrame(features_pca[:, :3], columns=['PC1', 'PC2', 'PC3'])

# Gráfico 3D interactivo
fig = px.scatter_3d(df_pca, x='PC1', y='PC2', z='PC3',
                    opacity=0.6,
                    title="Proyección PCA en 3D (95% varianza explicada)",
                    width=800, height=600)

fig.update_traces(marker=dict(size=3))
fig.show()

#### Porcentaje de varianza explicada

Finalmente, se imprime el porcentaje total de varianza que explican las tres primeras componentes principales. Esto permite verificar cuánta información original está siendo conservada en la proyección reducida.


In [48]:
explained_variance = pca.explained_variance_ratio_
print(f"Varianza acumulada (primeras 10 PCs): {explained_variance[:].sum():.2%}")

print(f"Número de componentes seleccionadas: {pca.n_components_}")

Varianza acumulada (primeras 10 PCs): 95.11%
Número de componentes seleccionadas: 10


## Entrenamiento del Modelo: Clustering con K-Means

Una vez extraídas las características y reducida su dimensionalidad mediante PCA, se procede a aplicar un algoritmo de clustering para identificar patrones latentes en los datos.

## ¿Por qué se usa K-Means y no otros métodos de clustering?

Para este caso específico, se opta por **K-Means** frente a otros algoritmos de clustering como el jerárquico o DBSCAN, por las siguientes razones:

### Ventajas de K-Means en este contexto:

1. **Escalabilidad y eficiencia**:
   - Se trabaja con un número elevado de muestras (ventanas), lo que hace que K-Means sea más adecuado por su bajo coste computacional.
   - Algoritmos como el clustering jerárquico tienen complejidad cuadrática, lo que los vuelve poco prácticos en datasets medianos o grandes.

2. **Dimensionalidad moderadamente alta**:
   - Aunque se aplica reducción de dimensionalidad (PCA), las características aún ocupan un espacio con decenas o centenas de dimensiones.
   - K-Means se adapta mejor a este tipo de espacios, mientras que DBSCAN sufre con la maldición de la dimensionalidad, donde la noción de “densidad” pierde eficacia.

3. **Forma de los clusters**:
   - Se espera que los datos se agrupen de forma aproximadamente esférica o convexa debido a la naturaleza de las características extraídas (estadísticas, frecuencia, movilidad, etc.).
   - Esto se alinea con la suposición implícita de K-Means, mientras que DBSCAN se diseñó para clusters de forma arbitraria, lo cual no es tan necesario en este caso.

4. **Estimación clara del número de clusters (K)**:
   - El método del codo proporciona una forma visual y efectiva de estimar el número óptimo de clusters.
   - DBSCAN requiere elegir valores de `eps` y `min_samples`, lo que suele ser menos intuitivo y más sensible a la escala.

### Conclusión:
K-Means ofrece una combinación ideal de simplicidad, eficiencia y compatibilidad con la estructura de los datos extraídos. Por ello, resulta la mejor opción frente a alternativas como DBSCAN o clustering jerárquico en este escenario.



## Selección del número óptimo de clusters: Método del Codo

Antes de aplicar K-Means, es necesario decidir cuántos grupos (clusters) queremos formar. Para ello, utilizamos el **método del codo**, una técnica visual que evalúa la inercia del modelo para diferentes valores de K (número de clusters).

### ¿Qué es la inercia?

La **inercia** es la suma de las distancias cuadradas entre cada punto y el centro de su cluster asignado. Un valor menor indica que los puntos están más cerca de sus respectivos centroides.

### ¿Cómo funciona el método del codo?

1. Se entrena K-Means con diferentes valores de `k` (número de clusters).
2. Se grafica la inercia resultante para cada valor.
3. Se busca el “codo” en la curva: el punto donde la reducción de la inercia comienza a ser marginal al aumentar `k`.

Este punto de inflexión es una buena estimación del número óptimo de clusters, ya que equilibra **compacidad** (baja inercia) y **simplicidad** (menor número de grupos).


In [49]:
inertia = []
K = range(1, 11)

for k in K:
    kmeans = KMeans(n_clusters=k, random_state=42)
    kmeans.fit(features_pca)
    inertia.append(kmeans.inertia_)

# Crear DataFrame para Plotly
df_elbow = pd.DataFrame({'Número de Clusters': list(K), 'Inercia': inertia})

# Gráfico interactivo
fig = px.line(df_elbow, x='Número de Clusters', y='Inercia', markers=True,
              title='Método del Codo para elegir K',
              labels={'Inercia': 'Suma de errores cuadrados'},
              width=700, height=500)

fig.update_traces(line=dict(color='royalblue'))
fig.update_layout(xaxis=dict(dtick=1), hovermode='x unified')
fig.show()

> En la gráfica del método del codo se observa un cambio notable en la pendiente de la curva hasta **K = 4**, a partir del cual las mejoras en la reducción del error cuadrático son marginales. Sin embargo, al analizar las métricas internas de validación, **K = 3** ofrece una mejor cohesión y separación entre los grupos. Por tanto, se selecciona **K = 3** como número óptimo de clusters, priorizando la calidad del agrupamiento y la claridad en la interpretación de los resultados.


### Entrenamiento con KMeans

En esta celda, se entrena un modelo de clustering utilizando el algoritmo **KMeans** sobre los datos previamente reducidos mediante **PCA**. Se define el número de clusters como 4 y se establece una semilla aleatoria (`random_state=42`) para asegurar la **reproducibilidad de los resultados**. A continuación, se ajusta el modelo a los datos transformados (`features_pca`) y se obtienen las **etiquetas de cluster** para cada muestra.


In [50]:

# Inicializamos el modelo KMeans con 3 clusters y una semilla aleatoria para reproducibilidad
kmeans = KMeans(n_clusters=3, random_state=42)

# Aplicamos el algoritmo KMeans a los datos del (PCA)
labels = kmeans.fit_predict(features_pca)


### Visualización de clusters en espacio reducido (PCA 3D)

Aunque cada ventana de movimiento está originalmente representada por **1080 características**, se ha aplicado una **reducción de dimensionalidad mediante PCA** para proyectar los datos en un espacio de solo tres componentes principales.  
Esta visualización en 3D **no refleja con precisión el espacio de características completo**, pero permite observar agrupamientos aproximados y relaciones estructurales entre los datos tras la reducción.  
Los puntos están coloreados según el **cluster asignado por KMeans**, y esta proyección ayuda a identificar posibles patrones o solapamientos entre grupos.



In [51]:
# Verificar las dimensiones
print(f"Dimensiones de features_pca: {features_pca.shape}")
print(f"Número de etiquetas: {len(labels)}")

# Verifica que labels tenga la longitud correcta
assert len(labels) == features.shape[0], "Mismatch entre labels y muestras de PCA"

# Crear DataFrame 
df_clusters = pd.DataFrame(features_pca[:, :3], columns=['PC1', 'PC2', 'PC3'])
df_clusters['Cluster'] = labels

# Crear gráfico 3D interactivo
fig = px.scatter_3d(df_clusters, 
                    x='PC1', y='PC2', z='PC3',
                    color='Cluster',
                    title='Visualización 3D de Clusters usando PCA',
                    labels={'PC1': 'Primera Componente Principal',
                           'PC2': 'Segunda Componente Principal', 
                           'PC3': 'Tercera Componente Principal',
                           'Cluster': 'Cluster'},
                    width=900, height=700)

# Personalizar diseño
fig.update_traces(marker=dict(size=3))
fig.update_layout(
    scene = dict(
        xaxis_title='PC1',
        yaxis_title='PC2',
        zaxis_title='PC3'
    ),
    showlegend=True
)

fig.show()


Dimensiones de features_pca: (3792, 10)
Número de etiquetas: 3792


## Evaluación del Clustering

Para evaluar la calidad de los agrupamientos generados por el algoritmo de clustering, se utilizaron las siguientes métricas:

- **Silhouette Score**: mide la coherencia interna de cada cluster (entre -1 y 1).
- **Calinski-Harabasz Index**: evalúa la separación entre clusters (cuanto mayor, mejor).
- **Davies-Bouldin Index**: mide la dispersión interna y separación entre clusters (cuanto menor, mejor).

A continuación se muestran los valores obtenidos tras aplicar el algoritmo de clustering seleccionado.


In [52]:
# 1. Calcular métricas
sil_score = silhouette_score(features_pca, labels)
calinski_score = calinski_harabasz_score(features_pca, labels)
davies_score = davies_bouldin_score(features_pca, labels)

# 2. Mostrar resultados
print("📊 Métricas de evaluación del clustering:")
print(f"Silhouette Score:        {sil_score:.4f}")
print(f"Calinski-Harabasz Index: {calinski_score:.4f}")
print(f"Davies-Bouldin Index:    {davies_score:.4f}")

📊 Métricas de evaluación del clustering:
Silhouette Score:        0.4031
Calinski-Harabasz Index: 3130.9645
Davies-Bouldin Index:    0.8557


| Métrica                  | Valor     | Evaluación realista                                                                                          |
| ------------------------ | --------- | ------------------------------------------------------------------------------------------------------------ |
| **Silhouette Score**     | `0.4031`  | **Buena**. Muestra una separación razonable entre grupos y buena cohesión interna, aunque es mejorable.                          |
| **Calinski-Harabasz**    | `3130.96` | **Muy buena**. Indica que los clusters están bien definidos y separados.                                     |
| **Davies-Bouldin Index** | `0.8557`  | **Excelente**. Un valor inferior a 1.0 indica una separación clara y sin solapamientos excesivos.           |


## Interpretacion de los resultados

In [53]:
# Crear DataFrame con resultados de PCA y etiquetas
columns_pca = [f'PC{i+1}' for i in range(features_pca.shape[1])]
df_pca_clusters = pd.DataFrame(features_pca, columns=columns_pca)
df_pca_clusters['cluster'] = labels

# Calcular estadísticas por cluster
mean_by_cluster = df_pca_clusters.groupby('cluster').mean().round(3)
std_by_cluster = df_pca_clusters.groupby('cluster').std().round(3)
min_by_cluster = df_pca_clusters.groupby('cluster').min().round(3)
max_by_cluster = df_pca_clusters.groupby('cluster').max().round(3)
var_by_cluster = df_pca_clusters.groupby('cluster').var().round(3)

# 🔍 Seleccionar las componentes más influyentes (con mayor desviación estándar total)
# Se calcula usando todas las filas, ignorando la columna 'cluster'
top_pcs = df_pca_clusters.drop(columns='cluster').std().sort_values(ascending=False).head(10).index.tolist()

print(f" Mostrando solo las componentes más influyentes: {top_pcs}")

# Mostrar resumen por cluster solo para las top PCs
for cluster_id in sorted(df_pca_clusters['cluster'].unique()):
    print(f"\n Resumen del Cluster {cluster_id}")
    resumen = pd.concat([
        mean_by_cluster.loc[cluster_id][top_pcs].to_frame(name='Media'),
        std_by_cluster.loc[cluster_id][top_pcs].to_frame(name='Desviación'),
        min_by_cluster.loc[cluster_id][top_pcs].to_frame(name='Mínimo'),
        max_by_cluster.loc[cluster_id][top_pcs].to_frame(name='Máximo'),
        var_by_cluster.loc[cluster_id][top_pcs].to_frame(name='Varianza')
    ], axis=1)
    display(resumen)


 Mostrando solo las componentes más influyentes: ['PC1', 'PC2', 'PC3', 'PC4', 'PC5', 'PC6', 'PC7', 'PC8', 'PC9', 'PC10']

 Resumen del Cluster 0


Media  Desviación   Mínimo   Máximo  Varianza
PC1   -0.384      31.073  -77.301   79.971   965.550
PC2  -27.148      28.624 -139.785   62.915   819.319
PC3    2.416      14.645  -50.152  132.595   214.463
PC4   -0.264      11.952  -24.518  162.472   142.853
PC5    0.425      10.193 -115.701   45.617   103.887
PC6   -1.222       9.581  -20.802   43.394    91.802
PC7   -0.103       6.444  -21.265   38.292    41.520
PC8   -0.078       5.241  -17.687   21.706    27.463
PC9    0.061       5.498  -28.563   20.379    30.229
PC10   0.012       5.273  -16.220   43.817    27.803


 Resumen del Cluster 1


Media  Desviación  Mínimo   Máximo  Varianza
PC1   96.271      43.375   1.212  215.436  1881.395
PC2   42.907      36.905 -32.355  134.108  1361.971
PC3   -3.601      15.739 -42.371   45.047   247.727
PC4    0.407       9.388 -25.049   35.662    88.129
PC5   -0.125       5.522 -23.653   17.644    30.487
PC6    2.260       4.855 -12.871   22.827    23.570
PC7    0.669       6.298 -21.990   19.977    39.666
PC8   -0.036       6.488 -17.194   21.841    42.089
PC9   -0.114       4.770 -13.116   14.588    22.751
PC10   0.062       4.099 -12.364   14.517    16.801


 Resumen del Cluster 2


Media  Desviación   Mínimo   Máximo  Varianza
PC1  -99.169      42.482 -223.202   -3.003  1804.733
PC2   42.178      37.440  -30.450  139.384  1401.726
PC3   -3.980      15.610  -43.665   39.934   243.664
PC4    0.421       9.229  -25.689   20.026    85.177
PC5   -1.232       3.883  -14.110   14.789    15.077
PC6    1.557       5.430  -12.984   22.032    29.484
PC7   -0.369       6.381  -19.423   18.757    40.723
PC8    0.287       6.898  -15.302   27.042    47.586
PC9   -0.076       4.863  -14.165   14.075    23.648
PC10  -0.102       4.248  -11.332   18.208    18.045

In [54]:
# Seleccionar las PCs que quieres mostrar
pcs_to_plot = ['PC1', 'PC2', 'PC3', 'PC4', 'PC5']

# Reorganizar el DataFrame en formato largo (long-form)
df_long = df_pca_clusters.melt(id_vars='cluster', value_vars=pcs_to_plot,
                               var_name='Componente', value_name='Valor')

# Convertir 'cluster' a string si quieres que salga como categoría en la leyenda
df_long['cluster'] = df_long['cluster'].astype(str)

# Crear gráfico interactivo
fig = px.box(df_long,
             x='Componente',
             y='Valor',
             color='cluster',
             title='Distribución de componentes principales por cluster',
             points=0,  # O 'outliers' para mostrar solo los valores atípicos
             color_discrete_sequence=px.colors.qualitative.Set2)

fig.update_layout(boxmode='group')  # Agrupar por cluster
fig.show()


### Interpretación de los clusters basada en las componentes principales

#### Cluster 0
- Valores centrados en torno a 0 en **PC1** y negativos en **PC2**, lo que sugiere un patrón de movimiento moderado y equilibrado.
- En **PC3**, la media es positiva, indicando cierta activación de componentes relacionadas con movimiento del tren superior o balanceo corporal.
- Este cluster podría representar **una marcha estable y sin desplazamientos extremos**, posiblemente el patrón más estándar entre los grupos.

#### Cluster 1
- Media **altamente negativa en PC1** y **positiva en PC2**, con gran varianza en ambas.
- Este patrón sugiere movimientos más **asimétricos o intensos**, especialmente en el eje capturado por PC2.
- La baja activación en componentes más altas (PC5–PC10) podría indicar menor complejidad o variabilidad en otras partes del cuerpo.
- Posiblemente representa un tipo de marcha **con mayor desplazamiento lateral o rotación del tronco**.

#### Cluster 2
- Media **muy positiva en PC1** (opuesta a Cluster 1) y también **positiva en PC2**, pero con menos dispersión.
- Este grupo muestra también valores ligeramente más altos en **PC6 y PC7**, lo que puede relacionarse con **movimientos más expresivos o flexiones de piernas o brazos**.
- El conjunto de valores sugiere un patrón de marcha más **amplio o energético**, pero más regular que el de Cluster 1.

---

En conjunto, los tres clusters representan **tres estilos diferenciados de marcha o movimiento corporal**, donde PC1 y PC2 juegan el papel más importante en la separación de grupos.


## Entrenamiento sin aplicar PCA

Esto lo hacemos para mantener toda la información original de las características extraídas, sin reducción dimensional. Aunque PCA puede ayudar a visualizar y acelerar el entrenamiento, también puede ocultar relaciones relevantes entre las variables originales. Por eso, en este enfoque, entrenamos el modelo de clustering directamente sobre el conjunto completo de características para preservar al máximo la estructura de los datos y facilitar una posterior interpretación detallada.


Lectura del archivo `features.csv` que contiene las características extraídas de las ventanas. Se muestra su forma y primeras filas.



In [55]:
# Leer el archivo CSV de características
df_features = pd.read_csv('features.csv')
print("Dimensiones del DataFrame:", df_features.shape)
print("\nPrimeras 5 filas:")
print(df_features.head())

Dimensiones del DataFrame: (3792, 1080)

Primeras 5 filas:
   feature_0  feature_1  feature_2  feature_3  feature_4  feature_5  \
0        0.0        0.0        0.0        0.0        0.0        0.0   
1        0.0        0.0        0.0        0.0        0.0        0.0   
2        0.0        0.0        0.0        0.0        0.0        0.0   
3        0.0        0.0        0.0        0.0        0.0        0.0   
4        0.0        0.0        0.0        0.0        0.0        0.0   

   feature_6  feature_7  feature_8  feature_9  ...  feature_1070  \
0        0.0        0.0        0.0        0.0  ...      0.013154   
1        0.0        0.0        0.0        0.0  ...      0.113696   
2        0.0        0.0        0.0        0.0  ...      0.100105   
3        0.0        0.0        0.0        0.0  ...      0.119487   
4        0.0        0.0        0.0        0.0  ...      0.101107   

   feature_1071  feature_1072  feature_1073  feature_1074  feature_1075  \
0      0.049629          18.0 

Aplicación del método del codo para estimar el número óptimo de clusters usando KMeans. Visualización interactiva de la inercia por número de clusters.


In [56]:
inertia = []
K = range(1, 11)

for k in K:
    kmeans = KMeans(n_clusters=k, random_state=42)
    kmeans.fit(df_features)
    inertia.append(kmeans.inertia_)

# Crear DataFrame para Plotly
df_elbow = pd.DataFrame({'Número de Clusters': list(K), 'Inercia': inertia})

# Gráfico interactivo
fig = px.line(df_elbow, x='Número de Clusters', y='Inercia', markers=True,
              title='Método del Codo para elegir K',
              labels={'Inercia': 'Suma de errores cuadrados'},
              width=700, height=500)

fig.update_traces(line=dict(color='royalblue'))
fig.update_layout(xaxis=dict(dtick=1), hovermode='x unified')
fig.show()


> Como se puede ver en la grafica la mejor opcion es el 3.

Entrenamiento del modelo KMeans con 3 clusters y obtención de las etiquetas de agrupamiento.


In [57]:

# Inicializamos el modelo KMeans con 3 clusters y una semilla aleatoria para reproducibilidad
kmeans = KMeans(n_clusters=3, random_state=42)

# Aplicamos el algoritmo KMeans a los datos
labels = kmeans.fit_predict(df_features)


Cálculo y visualización del número total de características utilizadas en el clustering.


In [58]:
n_caracteristicas = df_features.shape[1]
print("Número de características:", n_caracteristicas)


Número de características: 1080


Selección de las 3 características con mayor varianza para representar visualmente los clusters en 3D usando Plotly.


In [59]:
# Escoger columnas con mayor varianza
variancias = np.var(df_features, axis=0)

# Obtener las 3 columnas con mayor varianza
top3_names = df_features.var().sort_values(ascending=False).head(3).index.tolist()

df_clusters = df_features[top3_names].copy()
df_clusters.columns = ['Feature1', 'Feature2', 'Feature3'] 
df_clusters['Cluster'] = labels

# Añadir información estadística a los hover labels
hover_data = {
    'Feature1': ':.2f',
    'Feature2': ':.2f', 
    'Feature3': ':.2f',
    'Cluster': True
}

fig = px.scatter_3d(
    df_clusters,
    x='Feature1', y='Feature2', z='Feature3',
    color='Cluster',
    title='Visualización 3D de Clusters - Características con Mayor Varianza',
    labels={
        'Feature1': f'Característica 1 ({top3_names[0]})',
        'Feature2': f'Característica 2 ({top3_names[1]})', 
        'Feature3': f'Característica 3 ({top3_names[2]})',
        'Cluster': 'Cluster'
    },
    hover_data=hover_data,
    width=900, height=700
)

# Mejorar visualización
fig.update_traces(marker=dict(size=4, opacity=0.7))
fig.update_layout(
    scene=dict(
        xaxis_title=f'Feature1 ({top3_names[0]})',
        yaxis_title=f'Feature2 ({top3_names[1]})',
        zaxis_title=f'Feature3 ({top3_names[2]})'
    ),
    showlegend=True,
    legend_title_text='Clusters'
)

# Añadir anotaciones con estadísticas
for i in range(3):
    cluster_stats = df_clusters[df_clusters['Cluster']==i].describe()
    fig.add_annotation(
        x=0.95, y=0.9-i*0.1, 
        text=f'Cluster {i}: n={len(df_clusters[df_clusters.Cluster==i])}',
        showarrow=False,
        xref='paper', yref='paper',
        font=dict(size=10)
    )

fig.show()

Evaluación cuantitativa del clustering mediante métricas estándar: Silhouette Score, Calinski-Harabasz y Davies-Bouldin.


In [60]:
# 1. Calcular métricas
sil_score = silhouette_score(df_features, labels)
calinski_score = calinski_harabasz_score(df_features, labels)
davies_score = davies_bouldin_score(df_features, labels)

# 2. Mostrar resultados
print("📊 Métricas de evaluación del clustering:")
print(f"Silhouette Score:        {sil_score:.4f}")
print(f"Calinski-Harabasz Index: {calinski_score:.4f}")
print(f"Davies-Bouldin Index:    {davies_score:.4f}")

📊 Métricas de evaluación del clustering:
Silhouette Score:        0.3724
Calinski-Harabasz Index: 2755.5093
Davies-Bouldin Index:    0.9232


### 📊 Evaluación del Clustering

| Métrica                  | Valor     | Evaluación realista                                                                                          |
|--------------------------|-----------|--------------------------------------------------------------------------------------------------------------|
| **Silhouette Score**     | `0.3724`  | **Aceptable**. Indica una separación moderada entre grupos, aunque se puede mejorar la cohesión o separación. |
| **Calinski-Harabasz**    | `2755.51` | **Buena**. Sugiere que los clusters están razonablemente bien definidos y separados.                         |
| **Davies-Bouldin Index** | `0.9232`  | **Muy buena**. Un valor inferior a 1.0 indica separación clara con bajo solapamiento entre grupos.           |


### Interpretación de los clusters

En este apartado, como se hizo con los datos de PCA, se analizaran los clusters para saber que tipo de datos contienen

#### Interpretación de los clusters basada en las componentes principales



 
A continuación analizaremos las características más influyentes para cada cluster (con mayor desviación total):
 
1. Calculamos estadísticas básicas por cluster (media, desviación, mínimo, máximo y varianza)
2. Seleccionamos las 10 características con mayor desviación estándar total
3. Mostramos un resumen detallado de estas características para cada cluster

Esto nos permitirá entender qué características definen mejor cada grupo y cómo se diferencian entre sí.


In [61]:
# Crear DataFrame con las características y etiquetas
df_full_clusters = df_features.copy()
df_full_clusters['cluster'] = labels

# Calcular estadísticas por cluster
mean_by_cluster = df_full_clusters.groupby('cluster').mean().round(3)
std_by_cluster = df_full_clusters.groupby('cluster').std().round(3)
min_by_cluster = df_full_clusters.groupby('cluster').min().round(3)
max_by_cluster = df_full_clusters.groupby('cluster').max().round(3)
var_by_cluster = df_full_clusters.groupby('cluster').var().round(3)

#  Seleccionar las características más influyentes (con mayor desviación total)
top_features = df_full_clusters.drop(columns='cluster').std().sort_values(ascending=False).head(10).index.tolist()

print(f"Mostrando solo las características más influyentes: {top_features}")

# Mostrar resumen por cluster solo para las top features
for cluster_id in sorted(df_full_clusters['cluster'].unique()):
    print(f"\n Resumen del Cluster {cluster_id}")
    resumen = pd.concat([
        mean_by_cluster.loc[cluster_id][top_features].to_frame(name='Media'),
        std_by_cluster.loc[cluster_id][top_features].to_frame(name='Desviación'),
        min_by_cluster.loc[cluster_id][top_features].to_frame(name='Mínimo'),
        max_by_cluster.loc[cluster_id][top_features].to_frame(name='Máximo'),
        var_by_cluster.loc[cluster_id][top_features].to_frame(name='Varianza')
    ], axis=1)
    display(resumen)


Mostrando solo las características más influyentes: ['feature_1058', 'feature_1043', 'feature_866', 'feature_1057', 'feature_1042', 'feature_881', 'feature_701', 'feature_686', 'feature_127', 'feature_172']

 Resumen del Cluster 0


Media  Desviación  Mínimo   Máximo  Varianza
feature_1058  61.829      29.442   0.005  129.578   866.828
feature_1043  62.465      28.915   0.007  129.797   836.092
feature_866    8.556       6.394   1.228  153.434    40.886
feature_1057   4.124       4.004   1.000   22.000    16.035
feature_1042   4.153       4.098   1.000   29.000    16.794
feature_881    8.314       5.862   1.084   61.444    34.359
feature_701    8.301       5.819   1.067   61.392    33.857
feature_686    8.518       5.709   1.219   59.038    32.598
feature_127    8.139       4.043   1.000   24.000    16.347
feature_172    8.044       3.915   1.000   23.000    15.330


 Resumen del Cluster 1


Media  Desviación   Mínimo   Máximo  Varianza
feature_1058   35.676      30.365    0.718  148.088   922.030
feature_1043  175.884      47.507  102.061  329.266  2256.890
feature_866     5.807       3.122    1.356   17.886     9.748
feature_1057    7.662       4.637    1.000   22.000    21.506
feature_1042   12.305       4.986    1.000   23.000    24.864
feature_881     4.819       2.594    0.801   17.554     6.727
feature_701     4.814       2.593    0.804   17.401     6.723
feature_686     5.798       3.116    1.356   17.915     9.708
feature_127    12.444       5.133    1.000   30.000    26.344
feature_172    12.276       4.928    1.000   26.000    24.288


 Resumen del Cluster 2


Media  Desviación   Mínimo   Máximo  Varianza
feature_1058  174.819      45.269  105.443  313.390  2049.314
feature_1043   40.202      33.835    0.958  167.263  1144.780
feature_866     4.992       2.656    0.912   26.051     7.054
feature_1057   12.460       5.028    1.000   29.000    25.279
feature_1042    7.496       4.669    1.000   23.000    21.798
feature_881     5.984       3.199    1.461   29.033    10.236
feature_701     5.973       3.128    1.462   20.752     9.782
feature_686     4.988       2.586    0.910   17.676     6.686
feature_127    12.590       5.044    1.000   26.000    25.446
feature_172    12.395       4.792    1.000   28.000    22.964

#### Conclusiones por cluster
- **Cluster 0**: Valores moderados y estables en la mayoría de las características. Representa un patrón base o movimientos suaves.

- **Cluster 1**: Alta activación en `feature_1043` y otras variables. Indica acciones intensas o picos de movimiento específicos.

- **Cluster 2**: Alta activación en `feature_1058` (opuesto al cluster 1). Refleja un tipo diferente de intensidad, posiblemente en otras articulaciones o momentos.

**Resumen**: `feature_1043` y `feature_1058` son las más discriminantes entre los clusters y definen dos tipos principales de comportamiento dinámico.


#### Visualización de la distribución de características
 
Para entender mejor cómo se distribuyen las características más influyentes en cada cluster, creamos un gráfico de cajas (boxplot) que nos permite:

- Visualizar la distribución completa de cada característica por cluster
- Comparar fácilmente los rangos y medianas entre clusters
- Identificar patrones y diferencias significativas
 
El gráfico agrupa las cajas por característica y las colorea por cluster, facilitando la comparación visual de cómo cada cluster se comporta respecto a las características más importantes.


In [62]:
# Reorganizar el DataFrame en formato largo (long-form)
df_long = df_full_clusters.melt(id_vars='cluster', value_vars=top_features,
                                var_name='Característica', value_name='Valor')

# Convertir 'cluster' a string para mejor visualización en leyendas
df_long['cluster'] = df_long['cluster'].astype(str)

# Crear gráfico interactivo
fig = px.box(df_long,
             x='Característica',
             y='Valor',
             color='cluster',
             title='Distribución de características más influyentes por cluster',
             points=0,  # 'outliers' si quieres verlos
             color_discrete_sequence=px.colors.qualitative.Set2)

fig.update_layout(boxmode='group')  # Agrupar por cluster
fig.show()


#### Análisis del gráfico de distribución

El gráfico de cajas nos permite observar varios patrones importantes:

- **feature_1058**: Muestra la mayor variabilidad y separación entre clusters
- Cluster 2: Valores muy altos (150-200)
- Clusters 0 y 1: Valores más bajos (25-75)
 
- **feature_1043**: Segunda característica más discriminante
    - Cluster 1: Valores elevados (75-125)
    - Clusters 0 y 2: Valores más bajos 
- **Características restantes**: Muestran menos variación entre clusters
   - Valores más estables y similares entre grupos
   - Menor poder discriminativo
 
Esta visualización confirma que `feature_1058` y `feature_1043` son las variables más importantes para distinguir entre clusters, con patrones claramente diferenciados para cada grupo.
